In [1]:
# data = "data/data-3d9Ex.csv"
import plotly.express as px
import pandas as pd
import geopandas as gpd
import numpy as np
import json
import datetime as dt

from dash import Dash, dcc, html, Input, Output
import dash_bootstrap_components as dbc
import os

colorscales = px.colors.named_colorscales()

In [2]:
## Local settings to be able to test the app in the user environment and for running as a report
URL_PREFIX = os.path.join("/", os.getenv("REPORT_URL"))
PORT = os.getenv("REPORT_PORT", 9000)
HOSTNAME = os.getenv("HOSTNAME")
SERVER_NAME = os.getenv("SERVERNAME")

In [3]:
# Hungary counties shapefile
# url = "https://maps.princeton.edu/download/file/stanford-dt251rh6351-shapefile.zip"

In [4]:
#!cd data && wget https://maps.princeton.edu/download/file/stanford-dt251rh6351-shapefile.zip  && unzip stanford-dt251rh6351-shapefile.zip

In [5]:
# read shp data into geopandas
gg = gpd.read_file("data/dt251rh6351.shp")
ggjson = gg.to_json()
# gg.head()

# We will need gejson
dggjson = json.loads(ggjson)

# Turns out one of the county's name is misspelled so we rename it for now in the dataframe
# [f['properties']['name_1'] for f in dggjson['features']]

## Heti adatok

### Letoltes
https://atlo.team/koronaterkep/#megyeibovebb

In [6]:
# https://www.eea.europa.eu/data-and-maps/data/eea-reference-grids-2/gis-files/hungary-shapefile
# Fertozottek szama kumulativ
url = "https://docs.google.com/spreadsheets/d/1djH-yUHLPwuEExCjiXS__6-8W2Yp_msFvShpL4bBcuM/export?format=xlsx&gid=1283792994"
# heti uj esetek szama
url = "https://docs.google.com/spreadsheets/d/1djH-yUHLPwuEExCjiXS__6-8W2Yp_msFvShpL4bBcuM/export?format=xlsx&gid=1332599659"
heti_df = pd.read_excel(url)         

heti_df['date'] = pd.to_datetime(heti_df['Dátum']) #, format='%y-%m-%d')
#heti_df = heti_df.drop(columns=['Dátum', 'Összesen'])

In [7]:
#Rename Győr to Gyor
heti_df = heti_df.rename(columns={'Győr-Moson-Sopron':'Gyor-Moson-Sopron'})

In [8]:
heti_df.set_index('date', inplace=True)

heti_df = heti_df.resample('7D').sum()

heti_df.index=range(13,13+len(heti_df.index))
heti_df = heti_df.transpose()
heti_df.head()

13     14     15     16     17     18    19     20   \
Bács-Kiskun            19.0    3.0    1.0    0.0    0.0    0.0   1.0    0.0   
Baranya                23.0    6.0    4.0    0.0    3.0    0.0   0.0    0.0   
Békés                   8.0    3.0    2.0    1.0    2.0    1.0  -6.0    0.0   
Borsod-Abaúj-Zemplén    7.0   38.0    8.0    9.0    3.0   -1.0   0.0   -3.0   
Budapest              317.0  386.0  299.0  284.0  198.0  103.0  94.0  103.0   

                       21    22   ...     146     147  148     149    150  \
Bács-Kiskun            0.0   0.0  ...   577.0   505.0  0.0   730.0  217.0   
Baranya                0.0   1.0  ...   658.0   537.0  0.0   661.0  257.0   
Békés                  0.0   0.0  ...   585.0   359.0  0.0   507.0  208.0   
Borsod-Abaúj-Zemplén   0.0   1.0  ...   658.0   495.0  0.0   575.0  179.0   
Budapest              64.0  58.0  ...  1819.0  1437.0  0.0  1977.0  835.0   

                        151    152     153     154     155  
Bács-Kiskun           216.0  184.0   177.0   184.0   197.0  
Baranya               204.0  182.0   193.0   232.0   354.0  
Békés                 199.0  228.0   204.0   239.0   226.0  
Borsod-Abaúj-Zemplén  174.0  158.0   174.0   195.0   205.0  
Budapest              786.0  795.0  1011.0  1171.0  1042.0  

[5 rows x 143 columns]

In [9]:
# Get the mean of the county's centroids
cc = gg.centroid

clon = cc.apply(lambda x: x.x).mean()
clat = cc.apply(lambda x: x.y).mean()

/tmp/ipykernel_723/3451946974.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  cc = gg.centroid


In [10]:
heti_df.index=heti_df.index.rename('name_1')

heti_df=heti_df.reset_index()

In [11]:
colorscale = [[0, 'rgb(166,206,227, 0.5)'],
                      [0.01, 'rgb(31,120,180,0.5)'],
                      [0.05, 'rgb(178,223,138,0.5)'],
                      [0.1, 'rgb(51,160,44,0.5)'],
                      [0.15, 'rgb(251,154,153,0.5)'],
                      [1, 'rgb(227,26,28,0.5)']
                     ]

In [16]:
maxinfect = heti_df.max(axis=1).max()

/tmp/ipykernel_723/344204418.py:1: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  maxinfect = heti_df.max(axis=1).max()


In [17]:
filtered_df = heti_df[['name_1', heti_df.columns[1]]]
# filtered_df=filtered_df.rename(columns={heti_df.index[0]:'sum'})
fig = px.choropleth_mapbox(filtered_df, geojson=dggjson, locations='name_1', color=heti_df.columns[1],
                           color_continuous_scale= colorscale,
                           #locationmode='geojson-id',
                           featureidkey='properties.name_1',
                           range_color=(0, maxinfect),
                           mapbox_style="carto-positron",
                           zoom=5.7, center = {"lat": clat, "lon": clon},
                           opacity=0.5,
                           labels={heti_df.columns[1]:'Megfertozodesek szama'}
                          )
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0});


In [19]:
SERVER_NAME=SERVER_NAME[1:]
SERVER_NAME

'k8plex-krft.vo.elte.hu'

In [20]:
print("You can access your report at %s/%s"%(SERVER_NAME, URL_PREFIX))

external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']
app = Dash(__name__, external_stylesheets=[dbc.themes.SANDSTONE], url_base_pathname=URL_PREFIX+"/")

app.layout = html.Div([
    html.H4("Az azonosított fertőzöttek száma megyénként"),

    dcc.Graph(id="graph", figure=fig),
    # dcc.Slider(heti_df.index[0], heti_df.index[-1], marks={i:i for i in range(heti_df.index[0], heti_df.index[-1],5)},
    #            value=heti_df.index[0],
    #            id='my-slider'
    # ),
    dcc.Slider(heti_df.columns[1], heti_df.columns[-1], marks={i:i for i in range(heti_df.columns[1], heti_df.columns[-1],5)},
               value=heti_df.columns[1],
               id='my-slider'
    ),

])

@app.callback(
    Output("graph", "figure"), 
    Input('my-slider', 'value'))

def update_figure(selected_week):
    
    filtered_df = heti_df[['name_1', selected_week]]
    #filtered_df=filtered_df.reset_index().rename(columns={selected_week:'sum','index':'name_1'})

    #filtered_df = heti_df[['name_1', heti_df.columns[1]]]
    # filtered_df=filtered_df.rename(columns={heti_df.index[0]:'sum'})
    fig = px.choropleth_mapbox(filtered_df, geojson=dggjson, locations='name_1', color=selected_week,
                           color_continuous_scale=colorscale,
                           #locationmode='geojson-id',
                                                            

                           featureidkey='properties.name_1',
                           range_color=(0, maxinfect),
                           mapbox_style="carto-positron",
                           zoom=5.7, center = {"lat": clat, "lon": clon},
                           opacity=0.5,
                           labels={selected_week:'Megfertozodesek szama'}
                          )
    fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0}, transition_duration=500)

    return fig

app.run_server(debug=False, port=PORT, host=HOSTNAME)

You can access your report at k8plex-krft.vo.elte.hu//notebook/test/wfct0p-jupyter
Dash is running on http://wfct0p-jupyter:9000/notebook/test/wfct0p-jupyter/

 * Serving Flask app "__main__" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://wfct0p-jupyter:9000/ (Press CTRL+C to quit)
157.181.172.118 - - [09/Feb/2023 23:23:57] "GET /notebook/test/wfct0p-jupyter/ HTTP/1.1" 200 -
157.181.172.118 - - [09/Feb/2023 23:23:58] "GET /notebook/test/wfct0p-jupyter/_dash-dependencies HTTP/1.1" 200 -
157.181.172.118 - - [09/Feb/2023 23:23:58] "GET /notebook/test/wfct0p-jupyter/_dash-layout HTTP/1.1" 200 -
157.181.172.118 - - [09/Feb/2023 23:23:59] "GET /notebook/test/wfct0p-jupyter/_dash-component-suites/dash/dcc/async-graph.js HTTP/1.1" 200 -
157.181.172.118 - - [09/Feb/2023 23:23:59] "GET /notebook/test/wfct0p-jupyter/_dash-component-suites/dash/dcc/async-slider.js HTTP/1.1" 304 -
157.181.172.118 - - [09/Feb/2023 23:23:59] "GET /notebook/test/wfct0p-jupyter/_dash-component-suites/dash/dcc/async-plotlyjs.js HTTP/1.1" 304 -
157.181.172.118 - - [09/Feb/2023 23:24:00] "POST /notebook/test/wfct0p-jupyter/_dash-update-component HTTP/1.1" 200 -
157.181.172.118 - - [09/Feb/2023 23:24:04] "POST /notebook/test/wfct0p-jupy